In [1]:
from confluent_kafka import Consumer
from confluent_kafka.serialization import SerializationContext, MessageField
from confluent_kafka.schema_registry.json_schema import JSONDeserializer
from confluent_kafka.schema_registry import SchemaRegistryClient,Schema
import pymongo
from pymongo import MongoClient

In [2]:
#CONFIGURATION DETAILS

API_KEY = 'LAMZT52YQ3KXOLCK'
ENDPOINT_SCHEMA_URL  = 'https://psrc-nx65v.us-east-2.aws.confluent.cloud'
API_SECRET_KEY = 'M9R2ELFp/CYUUc56U1H1vbsKyse1EtCNrR3qqGUpQ7F72gCRT62Lc5+jWpLid1oB'
BOOTSTRAP_SERVER = 'pkc-921jm.us-east-2.aws.confluent.cloud:9092'
SECURITY_PROTOCOL = 'SASL_SSL'
SSL_MACHENISM = 'PLAIN'
SCHEMA_REGISTRY_API_KEY = 'T6UDFASJDL3RKCWZ'
SCHEMA_REGISTRY_API_SECRET = 'KQNwg+/HbCglNBys5AeK542yYObZCV7IbYj1w0Fxo3E1sOQd3UZ1pzaTAYUQ+/Db'

In [3]:
#CONFIGURATION FUNCTIONS

def sasl_conf():

    sasl_conf = {'sasl.mechanism': SSL_MACHENISM,
                 # Set to SASL_SSL to enable TLS support.
                #  'security.protocol': 'SASL_PLAINTEXT'}
                'bootstrap.servers':BOOTSTRAP_SERVER,
                'security.protocol': SECURITY_PROTOCOL,
                'sasl.username': API_KEY,
                'sasl.password': API_SECRET_KEY
                }
    return sasl_conf



def schema_config():
    return {'url':ENDPOINT_SCHEMA_URL,
    
    'basic.auth.user.info':f"{SCHEMA_REGISTRY_API_KEY}:{SCHEMA_REGISTRY_API_SECRET}"

    }

In [4]:
def main(topic):

    schema_registry_conf = schema_config()
    schema_registry_client = SchemaRegistryClient(schema_registry_conf)
#     schema = Schema(schema_str, 'JSON')
#     print(schema_registry_client.register_schema('case-value', schema, normalize_schemas=False))
    latest_version = schema_registry_client.get_latest_version(topic+'-value')
    json_deserializer = JSONDeserializer(latest_version.schema)

    consumer_conf = sasl_conf()
    consumer_conf.update({
                     'group.id': 'group1',
                     'auto.offset.reset': "earliest"})

    consumer = Consumer(consumer_conf)
    consumer.subscribe([topic])
    list_of_dict = []
    
    
    
    while True:
        try:
            # SIGINT can't be handled when polling, limit timeout to 1 second.
            msg = consumer.poll(1.0)
            if msg is None:
                continue

            dic = json_deserializer(msg.value(), SerializationContext(msg.topic(), MessageField.VALUE))
            list_of_dict.append(dic)

            if dic is not None:
                print("User record {}: car: {}\n"
                      .format(msg.key(), dic))
        except KeyboardInterrupt:
            break
    return list_of_dict

    consumer.close()


In [5]:
restaurants = main('restaurants')

User record b'529fec68-a97c-4032-843b-a146829af2d5': car: {'Order Number': 16118, 'Order Date': '03/08/2019 20:25', 'Item Name': 'Plain Papadum', 'Quantity': 2, 'Product Price': 0.8, 'Total products': 6}

User record b'06203ce2-c410-43a5-8d0d-e260e33742b3': car: {'Order Number': 16118, 'Order Date': '03/08/2019 20:25', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 6}

User record b'1082691f-30ab-4f8e-9435-2a90a8997303': car: {'Order Number': 16117, 'Order Date': '03/08/2019 20:17', 'Item Name': 'Mushroom Rice', 'Quantity': 1, 'Product Price': 3.95, 'Total products': 7}

User record b'8ad990c8-40d1-46b6-95d0-18846a5f2693': car: {'Order Number': 16117, 'Order Date': '03/08/2019 20:17', 'Item Name': 'Saag Paneer', 'Quantity': 1, 'Product Price': 5.95, 'Total products': 7}

User record b'df112bab-226f-498e-a24e-c82b56ab503b': car: {'Order Number': 16114, 'Order Date': '03/08/2019 19:44', 'Item Name': 'Special Fried Rice', 'Quantity': 2, 'Product Price

User record b'c84bd8d1-e1fd-4270-a220-7e42f88b0ce4': car: {'Order Number': 12940, 'Order Date': '14/01/2019 17:40', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 10}

User record b'45b79db8-fdaf-4623-b7fa-960ab4d16ede': car: {'Order Number': 12936, 'Order Date': '13/01/2019 19:15', 'Item Name': 'Lime Pickle', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 9}

User record b'c7f73b2a-fc62-4282-a5ab-d704ddfe0c93': car: {'Order Number': 12928, 'Order Date': '13/01/2019 17:15', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 11}

User record b'db40d284-b02e-4aac-b6bd-82f3db6e7457': car: {'Order Number': 12898, 'Order Date': '11/01/2019 19:09', 'Item Name': 'Red Sauce', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 4}

User record b'eda5557c-4e37-46a2-aaf4-549e4797795b': car: {'Order Number': 12844, 'Order Date': '05/01/2019 19:54', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, '

User record b'0a4a5861-6f35-455b-b24a-a725bde309c1': car: {'Order Number': 9165, 'Order Date': '13/04/2018 17:31', 'Item Name': 'Mint Sauce', 'Quantity': 2, 'Product Price': 0.5, 'Total products': 11}

User record b'1b59b079-8580-49cb-bf82-6393fece563a': car: {'Order Number': 9165, 'Order Date': '13/04/2018 17:31', 'Item Name': 'Onion Chutney', 'Quantity': 3, 'Product Price': 0.5, 'Total products': 11}

User record b'038461b5-2986-42e3-bd3b-2e10017525bf': car: {'Order Number': 9160, 'Order Date': '11/04/2018 19:15', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 7}

User record b'92ca7d79-596a-4692-80bb-2b2826096925': car: {'Order Number': 9114, 'Order Date': '07/04/2018 18:14', 'Item Name': 'Red Sauce', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 5}

User record b'02b0361d-e072-4ac5-8e31-b0bb45ddc503': car: {'Order Number': 9099, 'Order Date': '06/04/2018 18:51', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total 

User record b'da415ba2-af2b-41e6-b59d-3fb65c276d30': car: {'Order Number': 2992, 'Order Date': '22/08/2016 18:58', 'Item Name': 'Mint Sauce', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 5}

User record b'5564b96d-777a-410b-9830-61098ed527b3': car: {'Order Number': 2989, 'Order Date': '21/08/2016 19:38', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 8}

User record b'1abaa963-64c0-43d2-8722-cc25ad59a5db': car: {'Order Number': 2985, 'Order Date': '21/08/2016 19:21', 'Item Name': 'Red Sauce', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 14}

User record b'08bda3ab-0377-4101-9999-6ca30f383746': car: {'Order Number': 2956, 'Order Date': '18/08/2016 19:55', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 5}

User record b'2530de2c-13fe-4948-b103-fee8ad7cef29': car: {'Order Number': 2942, 'Order Date': '15/08/2016 19:17', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total p

User record b'7fa6c628-91ea-4b6c-b007-5d44b11aa146': car: {'Order Number': 8327, 'Order Date': '27/01/2018 18:36', 'Item Name': 'Plain Papadum', 'Quantity': 4, 'Product Price': 0.8, 'Total products': 8}

User record b'8ae2dfb2-07c4-4788-ab44-486f0fb41bc1': car: {'Order Number': 8282, 'Order Date': '24/01/2018 17:37', 'Item Name': 'Plain Papadum', 'Quantity': 4, 'Product Price': 0.8, 'Total products': 4}

User record b'3be757bf-bab4-4285-b6ce-a2c73b5209d3': car: {'Order Number': 8268, 'Order Date': '21/01/2018 19:11', 'Item Name': 'Plain Papadum', 'Quantity': 4, 'Product Price': 0.8, 'Total products': 7}

User record b'4b603ed3-2ab4-46b2-bcd0-c2af442f7a99': car: {'Order Number': 8217, 'Order Date': '19/01/2018 17:39', 'Item Name': 'Plain Papadum', 'Quantity': 2, 'Product Price': 0.8, 'Total products': 6}

User record b'0e2ac7b9-0de9-4473-86f0-cb676cf8bf61': car: {'Order Number': 8202, 'Order Date': '17/01/2018 19:49', 'Item Name': 'Spicy Papadum', 'Quantity': 2, 'Product Price': 0.8, 'T

...

User record b'dd4989c0-6937-4c22-b7a0-dcea3dcf0e98': car: {'Order Number': 3222, 'Order Date': '24/09/2016 18:52', 'Item Name': 'Chicken Tikka Chilli Masala', 'Quantity': 1, 'Product Price': 8.95, 'Total products': 3}

User record b'19e93b74-89f7-4e62-96ea-0e7331ecde20': car: {'Order Number': 3218, 'Order Date': '24/09/2016 18:18', 'Item Name': 'Chicken Tikka (Main)', 'Quantity': 1, 'Product Price': 8.95, 'Total products': 15}

User record b'03362359-9766-4f89-b735-60b23035d4c0': car: {'Order Number': 3193, 'Order Date': '19/09/2016 19:25', 'Item Name': 'Chicken Tikka Masala', 'Quantity': 1, 'Product Price': 8.95, 'Total products': 10}

User record b'c741a6c6-c89d-46b6-b8c0-68f842590a5c': car: {'Order Number': 3190, 'Order Date': '19/09/2016 18:34', 'Item Name': 'Lamb Tikka Jalfrezi', 'Quantity': 1, 'Product Price': 8.95, 'Total products': 5}

User record b'74cdeefb-dfbc-4979-b1e4-2543c2b143f2': car: {'Order Number': 3187, 'Order Date': '18/09/2016 19:01', 'Item Name': 'Lamb Tikka Masa

User record b'c40cbfcc-34bd-47d6-ade9-5e63fac16053': car: {'Order Number': 14883, 'Order Date': '18/05/2019 17:30', 'Item Name': 'Chicken Balti', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 6}

User record b'9ae24670-d2a7-4074-8c1f-8043b5ccf34d': car: {'Order Number': 14858, 'Order Date': '17/05/2019 18:02', 'Item Name': 'Chicken Shashlick', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 7}

User record b'd672b865-1879-4f63-8058-2cfc272d5523': car: {'Order Number': 14848, 'Order Date': '16/05/2019 18:52', 'Item Name': 'Lamb Chilli Garlic', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 12}

User record b'7a53d253-463f-4870-b768-1c6639b58a76': car: {'Order Number': 14831, 'Order Date': '15/05/2019 20:42', 'Item Name': 'Chicken Balti', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 3}

User record b'82e00043-1a6f-4049-b05e-97c5b54d78e8': car: {'Order Number': 14825, 'Order Date': '15/05/2019 18:11', 'Item Name': 'Chicken Shashlick', 'Quantity': 1, '

User record b'25bf8a67-41ad-4291-a33c-a55161d68b76': car: {'Order Number': 8174, 'Order Date': '13/01/2018 18:41', 'Item Name': 'Lal Mirch Lamb', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 9}

User record b'dbe67176-2bc1-4494-9f47-41c9a8904ae8': car: {'Order Number': 8170, 'Order Date': '13/01/2018 17:57', 'Item Name': 'Chicken Biryani', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 9}

User record b'3d9b3427-08f5-48d3-9c08-3a545b7fb6bd': car: {'Order Number': 8166, 'Order Date': '13/01/2018 17:28', 'Item Name': 'Chicken Balti', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 6}

User record b'e85d5940-af7a-477b-acbe-5f4bcc2b2ab0': car: {'Order Number': 8134, 'Order Date': '10/01/2018 20:42', 'Item Name': 'Butter Chicken', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 4}

User record b'3c07bd98-4e82-437e-bcd1-ef2938e703c7': car: {'Order Number': 8132, 'Order Date': '10/01/2018 20:09', 'Item Name': 'Chicken Hari Mirch', 'Quantity': 1, 'Product Pr

User record b'4cd9677a-383b-4485-8f3d-f61dff278113': car: {'Order Number': 15425, 'Order Date': '20/06/2019 18:31', 'Item Name': 'Lamb Tikka Biryani', 'Quantity': 1, 'Product Price': 10.95, 'Total products': 3}

User record b'a61a6197-3a3b-49ac-bd37-6973533bdb67': car: {'Order Number': 15249, 'Order Date': '08/06/2019 19:13', 'Item Name': 'Chicken Tikka Biryani', 'Quantity': 1, 'Product Price': 10.95, 'Total products': 4}

User record b'd1698266-9777-47dd-ab95-32864ed1e399': car: {'Order Number': 15246, 'Order Date': '08/06/2019 18:20', 'Item Name': 'Paneer Tikka Balti', 'Quantity': 1, 'Product Price': 10.95, 'Total products': 5}

User record b'dc3d17db-f0d3-4124-b041-3a72c9ddd83a': car: {'Order Number': 15213, 'Order Date': '07/06/2019 18:12', 'Item Name': 'Lamb Tikka Biryani', 'Quantity': 1, 'Product Price': 10.95, 'Total products': 14}

User record b'1bab7ec8-5643-4f3e-9e6a-a24d331d4405': car: {'Order Number': 15174, 'Order Date': '04/06/2019 17:58', 'Item Name': 'Chicken Tikka Balt

User record b'0ea88723-b751-4bc1-8816-3d209367eba7': car: {'Order Number': 6617, 'Order Date': '03/09/2017 19:42', 'Item Name': 'Tandoori Mixed Grill', 'Quantity': 1, 'Product Price': 11.95, 'Total products': 6}

User record b'6e14093d-c22e-442f-aa68-dc83b2dd196b': car: {'Order Number': 6461, 'Order Date': '22/08/2017 15:45', 'Item Name': 'Tandoori Mixed Grill', 'Quantity': 2, 'Product Price': 11.95, 'Total products': 6}

User record b'8fa62ad7-19e1-4488-b401-dc2c2552e03d': car: {'Order Number': 6414, 'Order Date': '18/08/2017 18:17', 'Item Name': 'Tandoori Fish (Main)', 'Quantity': 1, 'Product Price': 11.95, 'Total products': 3}

User record b'abd753e1-99bd-4c74-9b57-b7423d80bc6c': car: {'Order Number': 6413, 'Order Date': '18/08/2017 18:13', 'Item Name': 'Tandoori Mixed Grill', 'Quantity': 1, 'Product Price': 11.95, 'Total products': 9}

User record b'005bf7d1-76f5-4a03-9f0c-1c7c8fad8442': car: {'Order Number': 6117, 'Order Date': '20/07/2017 21:21', 'Item Name': 'Madras', 'Quantity'

In [6]:
print(len(restaurants))

37467
